<a href="https://colab.research.google.com/github/robynoconnor/pubpol2130/blob/main/Week11.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
%config InlineBackend.figure_formats = ["retina"]

In [2]:
!pip install -q geopandas seaborn folium census

# Redlining

In [3]:
import folium
import geopandas as gpd
import matplotlib.pyplot as plt
import pandas as pd
import seaborn as sns

from branca.utilities import color_brewer
from census import Census

In [4]:
census = Census("", year=2020)

We'll be pulling data (and inspiration) from the extraordinary University of Richmond project on redlining called [Mapping Inequality](https://dsl.richmond.edu/panorama/redlining/).  You should absolutely check out their stuff and click around.

In [5]:
areas_gdf = gpd.read_file("https://dsl.richmond.edu/panorama/redlining/static/mappinginequality.gpkg")

In [6]:
areas_gdf

area_id        city state  city_survey         category grade label  \
0          244  Birmingham    AL         True             Best     A    A1   
1          193  Birmingham    AL         True             Best     A    A2   
2          206  Birmingham    AL         True             Best     A    A3   
3          203  Birmingham    AL         True  Still Desirable     B    B1   
4          189  Birmingham    AL         True  Still Desirable     B   B10   
...        ...         ...   ...          ...              ...   ...   ...   
10149     6518    Wheeling    WV         True        Hazardous     D    D4   
10150     6520    Wheeling    WV         True        Hazardous     D    D5   
10151     6516    Wheeling    WV         True        Hazardous     D    D6   
10152     6512    Wheeling    WV         True        Hazardous     D    D7   
10153     6513    Wheeling    WV         True        Hazardous     D    D8   

       residential  commercial  industrial     fill  \
0             True       False       False  #76a865   
1             True       False       False  #76a865   
2             True       False       False  #76a865   
3             True       False       False  #7cb5bd   
4             True       False       False  #7cb5bd   
...            ...         ...         ...      ...   
10149         True       False       False  #d9838d   
10150         True       False       False  #d9838d   
10151         True       False       False  #d9838d   
10152         True       False       False  #d9838d   
10153         True       False       False  #d9838d   

                                                geometry  
0      MULTIPOLYGON (((-86.75678 33.49754, -86.75653 ...  
1      MULTIPOLYGON (((-86.75867 33.50933, -86.76134 ...  
2      MULTIPOLYGON (((-86.75678 33.49754, -86.75692 ...  
3      MULTIPOLYGON (((-86.80111 33.48071, -86.80505 ...  
4      MULTIPOLYGON (((-86.74923 33.53333, -86.74971 ...  
...                                                  ...  
10149  MULTIPOLYGON (((-80.71985 40.06376, -80.71943 ...  
10150  MULTIPOLYGON (((-80.72854 40.06729, -80.7287 4...  
10151  MULTIPOLYGON (((-80.72216 40.06134, -80.72247 ...  
10152  MULTIPOLYGON (((-80.6474 40.04886, -80.64842 4...  
10153  MULTIPOLYGON (((-80.66614 40.0497, -80.66678 4...  

[10154 rows x 12 columns]

Now we'll grab a dataset of redlining grades transfered onto U.S. census tracts from what's called the HRI (Historical Redlining Indicator).  

Meier, Helen C.S., and Mitchell, Bruce C. . Historic Redlining Indicator for 2000, 2010, and 2020 US Census Tracts. Ann Arbor, MI: Inter-university Consortium for Political and Social Research [distributor], 2023-09-25. https://doi.org/10.3886/E141121V3
(see [ICPSR](https://www.openicpsr.org/openicpsr/project/141121/version/V3/view?path=/openicpsr/141121/fcr:versions/V3.2&type=project))

In [7]:
hri_gdf = gpd.read_file("https://raw.githubusercontent.com/PUBPOL-2130/notebooks/refs/heads/main/data/HRI2020.zip")

In [8]:
hri_gdf

OBJECTID_1  OBJECTID      GEOID20    ALAND20  AWATER20   INTPTLAT20  \
0               0         1  01097001502   848502.0       0.0  +30.6568785   
1               0         3  01073004502  2953269.0       0.0  +33.5071040   
2               0         4  01073004501   723960.0       0.0  +33.4983380   
3               0         6  01073002402  4990907.0       0.0  +33.5299121   
4               0         7  01073002401  3488479.0       0.0  +33.5209629   
...           ...       ...          ...        ...       ...          ...   
13483           0     16596  55079007900   534569.0   24150.0  +43.0661920   
13484           0     16597  55079008000   326024.0       0.0  +43.0674802   
13485           0     16598  55079007700   679121.0   21023.0  +43.0649318   
13486           0     16599  55079008100   278881.0       0.0  +43.0674717   
13487           0     16600  55079010600   290784.0       0.0  +43.0601361   

         INTPTLON20   CBSA10                      METRO_NAME  Shape_Leng  \
0      -088.0688375  33681.0                      Mobile, AL    0.043989   
1      -086.8031176  13820.0           Birmingham-Hoover, AL    0.077309   
2      -086.8072523  13820.0           Birmingham-Hoover, AL    0.039856   
3      -086.7865984  13820.0           Birmingham-Hoover, AL    0.102104   
4      -086.7775618  13820.0           Birmingham-Hoover, AL    0.101521   
...             ...      ...                             ...         ...   
13483  -087.8957527  33340.0  Milwaukee-Waukesha-West Allis,    0.037109   
13484  -087.9028298  33340.0  Milwaukee-Waukesha-West Allis,    0.024456   
13485  -087.8886201  33340.0  Milwaukee-Waukesha-West Allis,    0.038491   
13486  -087.9074384  33340.0  Milwaukee-Waukesha-West Allis,    0.023043   
13487  -087.9074988  33340.0  Milwaukee-Waukesha-West Allis,    0.023537   

       EQINTER20  Shape_Le_1  Shape_Area   HRI2020  RHRI2020  \
0              4    0.043989    0.000080  3.924200       3.9   
1              4    0.077309    0.000287  3.939468       3.9   
2              4    0.039856    0.000070  3.551947       3.6   
3              4    0.102104    0.000484  3.997646       4.0   
4              4    0.101521    0.000339  3.751425       3.8   
...          ...         ...         ...       ...       ...   
13483          4    0.037109    0.000062  3.956915       4.0   
13484          4    0.024456    0.000036  4.000000       4.0   
13485          3    0.038491    0.000077  3.000000       3.0   
13486          4    0.023043    0.000031  3.650345       3.7   
13487          4    0.023537    0.000032  3.901154       3.9   

                                                geometry  
0      POLYGON ((-88.07488 30.64997, -88.07459 30.650...  
1      POLYGON ((-86.81747 33.50731, -86.8174 33.5073...  
2      POLYGON ((-86.81556 33.49672, -86.81517 33.497...  
3      POLYGON ((-86.80414 33.52829, -86.80397 33.528...  
4      POLYGON ((-86.79666 33.5172, -86.79389 33.5185...  
...                                                  ...  
13483  POLYGON ((-87.9004 43.06418, -87.90038 43.0652...  
13484  POLYGON ((-87.90534 43.06421, -87.90533 43.065...  
13485  POLYGON ((-87.89505 43.06792, -87.89497 43.067...  
13486  POLYGON ((-87.90961 43.06425, -87.9096 43.0653...  
13487  POLYGON ((-87.90972 43.05672, -87.9097 43.0575...  

[13488 rows x 16 columns]

Let's look at NYC!

In [9]:
queens_bronx_areas_gdf = areas_gdf[(areas_gdf["city"] == "Queens") | (areas_gdf["city"] == "Bronx")].copy()
queens_bronx_areas_gdf["score"] = queens_bronx_areas_gdf["grade"].map({"A": 3, "B": 2, "C": 1, "D": 0})
queens_bronx_areas_gdf

area_id    city state  city_survey                    category grade  \
6271     2736   Bronx    NY         True                        Best     A   
6272     2738   Bronx    NY         True                        Best     A   
6273     2737   Bronx    NY         True             Still Desirable     B   
6274     2764   Bronx    NY         True             Still Desirable     B   
6275     2775   Bronx    NY         True             Still Desirable     B   
...       ...     ...   ...          ...                         ...   ...   
6812     2472  Queens    NY         True                   Hazardous     D   
6813     2473  Queens    NY         True                   Hazardous     D   
6814     2475  Queens    NY         True                   Hazardous     D   
6815     2474  Queens    NY         True                   Hazardous     D   
6816    11398  Queens    NY         True  Industrial and Commercial   None   

                           label  residential  commercial  industrial  \
6271                          A1         True       False       False   
6272                          A2         True       False       False   
6273                          B1         True       False       False   
6274                         B10         True       False       False   
6275                         B11         True       False       False   
...                          ...          ...         ...         ...   
6812                          D6         True       False       False   
6813                          D7         True       False       False   
6814                          D8         True       False       False   
6815                          D9         True       False       False   
6816  Industrial and Commercial         False        True        True   

         fill                                           geometry  score  
6271  #76a865  MULTIPOLYGON (((-73.90345 40.91062, -73.90615 ...    3.0  
6272  #76a865  MULTIPOLYGON (((-73.89916 40.89286, -73.89949 ...    3.0  
6273  #7cb5bd  MULTIPOLYGON (((-73.90652 40.9006, -73.90522 4...    2.0  
6274  #7cb5bd  MULTIPOLYGON (((-73.85101 40.85032, -73.84922 ...    2.0  
6275  #7cb5bd  MULTIPOLYGON (((-73.83816 40.85735, -73.83685 ...    2.0  
...       ...                                                ...    ...  
6812  #d9838d  MULTIPOLYGON (((-73.85912 40.75063, -73.86101 ...    0.0  
6813  #d9838d  MULTIPOLYGON (((-73.85262 40.75252, -73.85424 ...    0.0  
6814  #d9838d  MULTIPOLYGON (((-73.85494 40.74337, -73.8572 4...    0.0  
6815  #d9838d  MULTIPOLYGON (((-73.85494 40.74337, -73.85476 ...    0.0  
6816  #000000  MULTIPOLYGON (((-73.82061 40.57957, -73.82149 ...    NaN  

[215 rows x 13 columns]

Not a lot of grade A terrain in Queens and the Bronx!

In [10]:
queens_bronx_areas_gdf["grade"].value_counts()

grade
C    134
D     46
B     28
A      3
E      1
Name: count, dtype: int64

In [11]:
queens_bronx_map = folium.Map([40.65, -73.95], zoom_start=12)
queens_bronx_choro = folium.Choropleth(
    geo_data=queens_bronx_areas_gdf,
    name="choropleth",
    data=queens_bronx_areas_gdf,
    columns=["area_id", "score"],
    key_on="feature.properties.area_id",
    fill_color="RdYlGn",
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name="Historic Redlining Indicator",
)
queens_bronx_choro.color_scale.colors = list(reversed(queens_bronx_choro.color_scale.colors))
queens_bronx_choro.add_to(queens_bronx_map)
queens_bronx_map

We can grab data for three metro areas.  Two out of three were easily covered by a single `METRO_NAME` but we had to do a little more work to find the GEOIDs associated with Houston.  

In [13]:
metro_areas = {
    "NYC": hri_gdf[hri_gdf["METRO_NAME"] == "New York-Newark-Jersey City, N"],
    "LA": hri_gdf[hri_gdf["METRO_NAME"] == "Los Angeles-Long Beach, CA"],
    #"Houston": hri_gdf[hri_gdf["GEOID20"].str.startswith("48201")]
    "Birmingham": hri_gdf[hri_gdf["METRO_NAME"] == "Birmingham-Hoover, AL"],
}

In [14]:
def plot_hri(gdf, center, zoom):
    hri_map = folium.Map(center, zoom_start=zoom)

    # ensure colors
    def reverse_color_brewer(*args, **kwargs):
        return list(reversed(color_brewer(*args, **kwargs)))

    folium.features.color_brewer = reverse_color_brewer
    choro = folium.Choropleth(
        geo_data=gdf,
        name="choropleth",
        data=gdf,
        columns=["GEOID20", "HRI2020"],
        key_on="feature.properties.GEOID20",
        fill_color="RdYlGn",
        fill_opacity=0.7,
        line_opacity=0.2,
        legend_name="Historic Redlining Indicator",
    )
    folium.features.color_brewer = color_brewer
    choro.add_to(hri_map)
    return hri_map

In [15]:
plot_hri(metro_areas["NYC"], center=[40.65, -73.95], zoom=12)

In [ ]:
plot_hri(metro_areas["LA"], center=[34.06, -118.25], zoom=11)

In [ ]:
plot_hri(metro_areas["Houston"], center=[29.76, -95.36], zoom=12)

In [18]:
plot_hri(metro_areas["Birmingham"], center=[33, -86], zoom=12)

Now we'll start some data prep to attach income information to the dataframe, so we can compare old redlining with persistent income gaps.

In [ ]:
counties_by_metro_area = {
    metro_area: set(gdf["GEOID20"].str.slice(0, 5))
    for metro_area, gdf in metro_areas.items()
}
counties = set.union(*counties_by_metro_area.values())

In [ ]:
median_income_raw = []
for county_fips in counties:
    print(county_fips)
    median_income_raw += census.acs5.get(
        (
            "B06011_001E",  # median income
        ),
        geo={
            "for": "tract:*",
            "in": f"state:{county_fips[:2]} county:{county_fips[2:]}",
        },
        year=2022,
    )

In [ ]:
median_income_df = pd.DataFrame(median_income_raw).rename(
    columns={
        "B06011_001E": "median_income",
    }
)
median_income_df["geoid"] = (
    median_income_df["state"]
    + median_income_df["county"]
    + median_income_df["tract"]
)
median_income_df = median_income_df.set_index("geoid")
median_income_df = median_income_df[median_income_df["median_income"] > 0]  # filter out negative sentinel values

Let's make a scatterplot of housing grades vs. current income levels.

In [ ]:
for label, gdf in metro_areas.items():
    sns.regplot(
        data=median_income_df.join(gdf.set_index("GEOID20")["HRI2020"]),
        x="HRI2020",
        y="median_income",
        scatter_kws={"s": 10},
    )
    plt.xlabel("Historic Redlining Indicator")
    plt.ylabel("Median income")
    plt.title(f"Redlining vs. median income ({label} metro)")
    plt.show()

Next, we'll bring back "KDE plots," which are smooth curves that capture some of the information in a distribution in an intuitive way.  Let's look at NYC, LA, and Houston and examine the distribution of median income.

In [ ]:
displot_palette = list(reversed(color_brewer("RdYlGn")[:3] + color_brewer("RdYlGn")[5:]))

for label, gdf in metro_areas.items():
    df = median_income_df.join(gdf.set_index("GEOID20")["HRI2020"])
    df["Grade"] = df["HRI2020"].round().map({1: "A", 2: "B", 3: "C", 4: "D"})

    sns.displot(
        data=df,
        x="median_income",
        hue="Grade",
        kind="kde",
        fill=False,
        #alpha=0.15,
        height=5,
        aspect=2,
        palette=dict(zip(("A", "B", "C", "D"), displot_palette)),
        hue_order=("A", "B", "C", "D"),
    )

    plt.xlabel("Median income ($)")
    plt.title(f"Tract median income by approximate redlining grade ({label} metro)")
    plt.show()

    print("Medians of median income by grade:")
    print(df.groupby("Grade")["median_income"].median())

Now let's close out by comparing redlining grades to an index of "social vulnerability."  The SVI is an index that combines a number of factors drawn fron the ACS -- these include socioeconomic indicators (poverty, lack of health insurance), household characteristics (more elders and children, disability, low English proficiency), racial and ethnic minority status, and housing and transportation variables (no car, crowded living arrangements).

[CDC/ATSDR SVI 2022 Documentation](https://www.atsdr.cdc.gov/place-health/media/pdfs/2024/10/SVI2022Documentation.pdf) -- idea from ["From Redlining to Gentrification"](https://info.primarycare.hms.harvard.edu/perspectives/articles/redlining-gentrification-health-outcomes)

In [ ]:
social_vuln_df = pd.read_csv("https://svi.cdc.gov/Documents/Data/2022/csv/states/SVI_2022_US.csv").set_index("FIPS")
social_vuln_df.index = social_vuln_df.index.astype(str).str.zfill(11)

In [ ]:
social_vuln_df

In [ ]:
social_vuln_df = social_vuln_df[social_vuln_df["RPL_THEMES"] > 0]

In [ ]:
social_vuln_df["RPL_THEMES"]

In [ ]:
gdf.set_index("GEOID20")[["HRI2020", "geometry"]].join(median_income_df)

In [ ]:
for label, gdf in metro_areas.items():
    joined_gdf = gpd.GeoDataFrame(
        gdf.set_index("GEOID20")[["HRI2020", "geometry"]].join(median_income_df).join(social_vuln_df["RPL_THEMES"]),
        crs=gdf.crs,
    )
    fig, axes = plt.subplots(1, 3, figsize=(15, 45))
    kwds = dict(legend_kwds={'shrink': 0.06}, legend=True)
    joined_gdf.plot(column="HRI2020", ax=axes[0], **kwds)
    joined_gdf.plot(column="median_income", ax=axes[1], **kwds)
    joined_gdf.plot(column="RPL_THEMES", ax=axes[2], **kwds)

    axes[0].set_title("Historic Redlining Indicator")
    axes[1].set_title("Median income ($)")
    axes[2].set_title("Social Vulnerability Index")
    fig.suptitle(f"{label} metro", y=0.54, fontsize=16)

    for ax in axes:
        ax.set_axis_off()

# Homework 8, due Friday April 18 (extended deadline Tuesday April 22, 1:25pm)

**Warmup question**: switch to a different metro area and create a plot of the HRI, median income, and SVI for that area.

**Data product**: use this notebook to get curious about some aspect of redlining. Formulate a question and make a data product that addresses it. Briefly explain how you made it.

**Reading question**: this week I've assigned a very short reading by Richard Rothstein where he summarizes his 2017 book *The Color of Law* and discusses what it would look like to remediate the *de jure* segregation of the 20th century. In it, he discusses why the wealth gap is larger than the income gap. Cite a related passage from the reading, giving a page number.  Then briefly expand on Rothstein's argument about income vs. wealth (either amplifying or pushing back).